# Initial instructions

In [1]:
! pip install kaggle

In [2]:
from google.colab import files

In [3]:
files.upload()
! mkdir ~/.kaggle
! cp kaggle.json ~/.kaggle/
! chmod 600 ~/.kaggle/kaggle.json
! kaggle datasets download -d rounakbanik/the-movies-dataset

KeyboardInterrupt: ignored

In [ ]:
import os
if not os.path.isdir('/content/data/cleaned') :
    os.mkdir('/content/data/cleaned')

In [ ]:
! unzip '/content/the-movies-dataset.zip' -d '/content/data/raw'

Archive:  /content/the-movies-dataset.zip
  inflating: /content/data/raw/credits.csv  
  inflating: /content/data/raw/keywords.csv  
  inflating: /content/data/raw/links.csv  
  inflating: /content/data/raw/links_small.csv  
  inflating: /content/data/raw/movies_metadata.csv  
  inflating: /content/data/raw/ratings.csv  
  inflating: /content/data/raw/ratings_small.csv  


# Needed Imports

In [4]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import re

# Load datasets

In [28]:
metadata = pd.read_csv('/content/drive/MyDrive/Rec/data/cleaned/clean_metadata.csv')
credits = pd.read_csv('/content/drive/MyDrive/Rec/data/cleaned/clean_credits.csv')
keywords = pd.read_csv('/content/drive/MyDrive/Rec/data/cleaned/clean_keywords.csv')
links = pd.read_csv('/content/drive/MyDrive/Rec/data/raw/links.csv')
links = links[links['tmdbId'].notnull()]['tmdbId'].astype('int')

In [22]:
print('shape: {}'.format(metadata.shape))
print('columns: \n {}'.format(metadata.columns))
metadata.head(3)

shape: (45447, 30)
columns: 
 Index(['adult', 'budget', 'homepage', 'id', 'imdb_id', 'original_language',
       'original_title', 'overview', 'popularity', 'poster_path',
       'production_companies', 'release_date', 'revenue', 'runtime', 'status',
       'tagline', 'title', 'video', 'vote_average', 'vote_count',
       'name_belongs_to_collection', 'id_belongs_to_collection',
       'poster_path_belongs_to_collection',
       'backdrop_path_belongs_to_collection', 'name_genres', 'id_genres',
       'name_production_countries', 'iso_3166_1_production_companies',
       'name_production_companies', 'id_production_companies'],
      dtype='object')


adult    budget                              homepage     id    imdb_id  \
0  False  30000000  http://toystory.disney.com/toy-story    862  tt0114709   
1  False  65000000                                   NaN   8844  tt0113497   
2  False         0                                   NaN  15602  tt0113228   

  original_language    original_title  \
0                en         Toy Story   
1                en           Jumanji   
2                en  Grumpier Old Men   

                                            overview  popularity  \
0  Led by Woody, Andy's toys live happily in his ...   21.946943   
1  When siblings Judy and Peter discover an encha...   17.015539   
2  A family wedding reignites the ancient feud be...   11.712900   

                        poster_path  ... name_belongs_to_collection  \
0  /rhIRbceoE9lR4veEXuwCC2wARtG.jpg  ...       Toy Story Collection   
1  /vzmL6fP7aPKNKPRTFnZmiUfciyV.jpg  ...                        NaN   
2  /6ksm1sjKMFLbO7UY2i6G1ju9SML.jpg  ...  Grumpy Old Men Collection   

  id_belongs_to_collection  poster_path_belongs_to_collection  \
0                  10194.0   /7G9915LfUQ2lVfwMEEhDsn3kT4B.jpg   
1                      NaN                                NaN   
2                 119050.0   /nLvUdqgPgm3F85NMCii9gVFUcet.jpg   

   backdrop_path_belongs_to_collection                 name_genres  \
0     /9FBwqcd9IRruEDUrTdcaafOMKUq.jpg   Animation, Comedy, Family   
1                                  NaN  Adventure, Fantasy, Family   
2     /hypTnLot2z8wpFS7qwsQHW1uV8u.jpg             Romance, Comedy   

       id_genres name_production_countries  iso_3166_1_production_companies  \
0  16, 35, 10751  United States of America                               US   
1  12, 14, 10751  United States of America                               US   
2      10749, 35  United States of America                               US   

                           name_production_companies  id_production_companies  
0                            Pixar Animation Studios                        3  
1  TriStar Pictures, Teitler Film, Interscope Com...         559, 2550, 10201  
2                       Warner Bros., Lancaster Gate              6194, 19464  

[3 rows x 30 columns]

In [23]:
a = metadata['original_language'].value_counts()
a[a>10]

en    32260
fr     2437
it     1529
ja     1349
de     1079
es      994
ru      826
hi      508
ko      444
zh      409
sv      384
pt      316
cn      313
fi      295
nl      248
da      224
pl      219
tr      150
cs      130
el      113
no      106
fa      101
hu      100
ta       78
th       75
he       67
sr       63
ro       57
te       45
ar       39
ml       36
xx       33
hr       29
bn       29
mr       25
et       24
is       24
tl       23
id       20
lv       18
ka       18
sl       17
uk       16
bs       14
ca       12
Name: original_language, dtype: int64

# Constructing the dataset used for item based recommendation

In [24]:
keywords['id'] = keywords['id'].astype('int')
credits['id'] = credits['id'].astype('int')

In [32]:
metadata = metadata.merge(credits, on='id')
metadata = metadata.merge(keywords, on='id')

## Use only the available movies in TMDB

In [33]:
rec_data = metadata[metadata['id'].isin(links)].copy()
rec_data.shape

(45459, 45)

In [140]:
rec_data = rec_data.drop_duplicates(subset='id')

## Adding 'director' column

In [34]:
def is_float(string):
    try:
        float(string)
        return True
    except ValueError:
        return False

In [37]:
def directors_names(job_crew, index):
    if not isinstance(job_crew, float):
        jobs = job_crew.split(', ')
        director_indices = [i for i, job in enumerate(jobs) if job == 'Director']
        if director_indices:
            names = rec_data.loc[index, 'name_crew']
            if not isinstance(names, float):
                names = names.split(', ')
                director_names = [names[i] for i in director_indices]
                return ', '.join(director_names)
    return np.nan

In [38]:
for i in rec_data.index:
    rec_data.loc[i, 'director'] = directors_names(rec_data.loc[i, 'job_crew'], i)
rec_data['director']

0           John Lasseter
1            Joe Johnston
2           Howard Deutch
3         Forest Whitaker
4           Charles Shyer
               ...       
45454    Hamid Nematollah
45455            Lav Diaz
45456      Mark L. Lester
45457    Yakov Protazanov
45458       Daisy Asquith
Name: director, Length: 45459, dtype: object

# Generating the final dataset

In [84]:
rec_data = rec_data [['id', 'original_language', 'overview','tagline', 'title', 'name_genres', 'name_cast', 'name_keywords', 'director']]

In [87]:
rec_data = rec_data.replace(np.nan, '')

In [95]:
rec_data = rec_data.replace('', 'Not mentioned')

In [115]:
rec_data['description'] = 'Title: ' + rec_data['title'] + '. Director: ' + rec_data['director']  + '. Genres: ' + rec_data['name_genres'] + '. Overview: ' + rec_data['overview'] + ' Keywords: ' + rec_data['name_keywords'] + '. Language: ' + rec_data['original_language'] + '.'

In [128]:
def clean_text (text) :
    try:
        # Remove new line and tabs
        clean = text.replace("\n", " ")
        clean = clean.replace("\t", " ")
        clean = clean.replace("\r", " ")
        clean = clean.replace("Â\xa0", "")  # non-breaking space

        # Remove all punctuation and special characters
        # clean = re.sub(
        #     r"([^\s\w]|_)+", "", clean
        # )  # noqa W695 invalid escape sequence '\s'

        # If you want to keep some punctuation, see below commented out example
        clean = re.sub(r'([^,.:\s\w\-]|_)+','', clean)

        # Skip further processing if the text will be used in BERT tokenization

    except Exception:
        print("Cannot clean non-existent text")
        clean = ""

    return clean

In [130]:
rec_data['description'] = rec_data['description'].apply(clean_text)

In [141]:
final_rec_data = rec_data[['id', 'title', 'description']]
final_rec_data = final_rec_data.drop_duplicates(subset='id')

In [142]:
final_rec_data.shape

(45429, 3)

## Saving the dataset

In [143]:
final_rec_data.to_csv('/content/drive/MyDrive/Rec/data/cleaned/descriptions.csv', index=False)

# REC

In [5]:
d =  pd.read_csv('/content/drive/MyDrive/Rec/data/cleaned/descriptions.csv')

In [7]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel, cosine_similarity

tfidf = TfidfVectorizer(analyzer='word',ngram_range=(1, 2),min_df=0.0, stop_words='english')
tfidf_matrix = tfidf.fit_transform(d['description'])
# cosine_sim = cosine_similarity(tfidf_matrix, tfidf_matrix)
# cosine_sim = cosine_sim.astype(np.float16)


In [23]:
def recommender (title, num_recommends):
    idx = d[d['title'] == title].index[0]
    cosine_sim = cosine_similarity(tfidf_matrix[int(idx)], tfidf_matrix)
    similarity_scores = list(enumerate(cosine_sim[0]))
    similarity_scores = sorted(similarity_scores, key=lambda x: x[1], reverse=True)
    similarity_scores = similarity_scores[1: num_recommends + 1]
    movie_indices = [i[0] for i in similarity_scores]
    return d.iloc[movie_indices]['title']

In [2]:
! pip install scikit-surprise

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 772.0/772.0 kB 43.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for scikit-surprise: filename=scikit_surprise-1.1.3-cp310-cp310-linux_x86_64.whl size=3096320 sha256=ab360f2850ab501540eeccaf1058521f2c63a69cb989d9308e7f3d63bc789795
  Stored in directory: /root/.cache/pip/wheels/a5/ca/a8/4e28def53797fdc4363ca4af740db15a9c2f1595ebc51fb445
Successfully built scikit-surprise


In [3]:
import pandas as pd
from surprise import Dataset, SVD ,Reader
from sklearn.metrics.pairwise import linear_kernel, cosine_similarity
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from surprise.model_selection import cross_validate , KFold
from surprise import model_selection

In [9]:
from surprise import Dataset, Reader, SVD
from surprise.model_selection import train_test_split
from surprise.accuracy import rmse

# load data from a CSV file
data = pd.read_csv('/content/drive/MyDrive/Rec/data/raw/ratings_small.csv')

# define the Reader object
reader = Reader(rating_scale=(1, 5))

# load the data into the Dataset object
dataset = Dataset.load_from_df(data[['userId', 'movieId', 'rating']], reader)

# split the data into training and testing sets
trainset, testset = train_test_split(dataset, test_size=0.2)

# define the SVD algorithm
algo = SVD(n_factors=100, n_epochs=20)

# train the algorithm on the training set
algo.fit(trainset)

# make predictions on the testing set
predictions = algo.test(testset)

# evaluate the performance of the algorithm
rmse_score = rmse(predictions)
print('RMSE:', rmse_score)

# make recommendations for a given user
user_id = 24256
items_to_recommend = []
for item_id in data['movieId'].unique():
    predicted_rating = algo.predict(user_id, item_id).est
    if predicted_rating >= 4.8:
        items_to_recommend.append(item_id)
print('Items to recommend:', items_to_recommend)

RMSE: 0.8969
RMSE: 0.8968864510559503
Items to recommend: []


In [34]:
links = links.rename(columns={'imdbId' : 'imdb_id'})
links['movieId']

movieId  imdb_id   tmdbId
0        1   114709    862.0
1        2   113497   8844.0
2        3   113228  15602.0
3        4   114885  31357.0
4        5   113041  11862.0

In [27]:
links['imdb_id']=links['imdb_id'].astype(int)

In [36]:
2 in cr['id']

True

In [28]:
cr = cr.merge(links, on='imdb_id')

ValueError: ignored